# Feature Exploration

Given the [Kaggle Dataset on Lead Scoring](https://www.kaggle.com/datasets/amritachatterjee09/lead-scoring-dataset?select=Lead+Scoring.csv), I will first do some general EDA to discover potential trends within the data to determine possible next steps.

From the Kaggle site, X Education is education company selling online courses to industry professionals. The typical conversion rate is ~30%. The goal is to increase the conversion rate, with the CEO hoping to achieve a lead conversion rate of about 80%. Our task is to assign a lead score to each of the leads such that the customers with higher lead score *h* have a higher conversion chance (IE create a propensity score).

In [46]:
# Modules
import numpy as np
import pandas as pd
from pathlib import Path
import os
from ydata_profiling import ProfileReport

In [47]:
# Pull in data
raw_data = pd.read_csv(Path(os.getcwd()).parents[0].joinpath("data", "Lead Scoring.csv"))

# General EDA

Clearly, the goal of this exercise is to increase the conversion rate, making the `Converted` column our target variable.

To get a clear picture of how variables might relate to one another, I will be using the `ProfileReport` function to create an HTML page summarizing distributions, correlations, and other measures.

In [48]:
# Use ProfileReport to create HTML doc of general summary
profile = ProfileReport(raw_data, title = "Profiling Report")
profile.to_file("feature_eda.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [49]:
# Or run as follows:
profile.to_notebook_iframe()

In [50]:
print(f"{len(raw_data.columns)} Columns, Names: {raw_data.columns}")

37 Columns, Names: Index(['Prospect ID', 'Lead Number', 'Lead Origin', 'Lead Source',
       'Do Not Email', 'Do Not Call', 'Converted', 'TotalVisits',
       'Total Time Spent on Website', 'Page Views Per Visit', 'Last Activity',
       'Country', 'Specialization', 'How did you hear about X Education',
       'What is your current occupation',
       'What matters most to you in choosing a course', 'Search', 'Magazine',
       'Newspaper Article', 'X Education Forums', 'Newspaper',
       'Digital Advertisement', 'Through Recommendations',
       'Receive More Updates About Our Courses', 'Tags', 'Lead Quality',
       'Update me on Supply Chain Content', 'Get updates on DM Content',
       'Lead Profile', 'City', 'Asymmetrique Activity Index',
       'Asymmetrique Profile Index', 'Asymmetrique Activity Score',
       'Asymmetrique Profile Score',
       'I agree to pay the amount through cheque',
       'A free copy of Mastering The Interview', 'Last Notable Activity'],
      dtype='o

## `feature_eda.html` Analysis

THe `ProfileReport` gives some great insights as a first pass. Our dataset contains 37 variables and 9240 observations. We see that `Prospect ID` and `Lead Number` are both keys for the dataset. The `Do Not Call` variable only has 2 true instances, making it an easy variable to remove in our modeling process. Our target variable `Converted` shows that about 38.5% of people in this dataset convert, slightly higher than the 30% mentioned in the prompt.

### Questions

- What does `Select` mean? Guessing that's the default answer asking someone to select an option?
  - If so, probably can treat as `Missing` as well...

### Response Variable: `Converted`

- 38.5% converted / 71.5% did not

### Variables w/ High Correlation

- `Total Time Spent on Website` (0.426)
-  `Asymmetrique Activity Score` (0.419)
- `Lead Quality` (0.659)
- `Tags` (0.931)
- `Last Activity` (0.396)
- `Lead Source` (0.336)
- `Lead Origin` (0.325)
- `Current Occupation` (0.302)
- `Lead Profile` (0.379)
- `Last Notable Activity` (0.38)

### Variables Maybe Needing Preprocessing (Grouping)

- `Country`: 26.6% mssing, heavily favoring India, and all other countries are under 1%...
- `City`(?): Missing 15.4%, but seems to only apply to people in India
- `Last Notable Activity`: 16 total groups
- `Lead Profile`: Missing 29.3% of data
- `Lead Source`: Need to apply some data cleaning (EX: Google vs. google are treated differently)
- `Lead Quality`: 51.6% missing!
- `Tags`: 36.3% missing, many categories
- `What is your current occupation`: 29.1% missing, majority are `unemployed`, and other categories (`Working Professional` and `Student`) make up 10% - others are very small in #s
- `How did you hear about X Education`: 10 categories, 23.9% missing, most are `Select`
- `Specialization`: 15.6% missing, 21% `Select`, >20 categories
- `Last Activity`: >15 categories. However, many seem relevant (unsub, unreachable) - need to do more analysis
- `Page Views Per Visit`(?): many 0s, maybe interesting to see relationships between 0 vs. non-0, or if numerical better



### Variables to Remove

In general, we can exclude 13 variables (shown below + why).

- `I agree to pay the amount through cheque`: 1 value
- `Get updates on DM Content`: 1 value
- `Update me on Supply Chain Content`: 1 value
- `Receive More Updates About Our Courses`: 1 value
- `Through Recommendations`: only 7 Trues
- `Digital Advertisement`: only 4 Trues
- `Newspaper`: Only 1 True
- `X Education Forums`: Only 1 True
- `Newspaper Article`: only 2 true
- `Magazine`: only 1 true
- `Search`: Only 14 True
- `What matters most to you in choosing a course`: Only 3 categories, but 2 have under 5 total obs
- `Do Not Call`: only 2 Trues

In [51]:
data = raw_data.copy()
data = data.drop(["I agree to pay the amount through cheque",
                  "Get updates on DM Content",
                  "Update me on Supply Chain Content",
                  "Receive More Updates About Our Courses",
                  "Through Recommendations",
                  "Digital Advertisement",
                  "Newspaper",
                  "X Education Forums",
                  "Newspaper Article",
                  "Magazine",
                  "Search",
                  "What matters most to you in choosing a course",
                  "Do Not Call"], axis=1)

## Variable Preprocessing

Now, we'll be looking at the variables mentioned earlier that probably need preprocessing.

### Country

Because there are so many countries, it might be worth trying to combine countries together, rather than one-hot-encode each one.

First, let's look at each nation and compare conversion rates.

In [52]:
data.fillna("Missing").groupby(["Country", "Converted"])["Converted"].count()

Country               Converted
Asia/Pacific Region   0               1
                      1               1
Australia             0              10
                      1               3
Bahrain               0               3
                      1               4
Bangladesh            0               1
                      1               1
Belgium               0               2
Canada                0               4
China                 0               2
Denmark               1               1
France                0               3
                      1               3
Germany               0               3
                      1               1
Ghana                 0               2
Hong Kong             0               3
                      1               4
India                 0            4091
                      1            2401
Indonesia             0               1
Italy                 0               2
Kenya                 0               1
Kuwait  

From the output above, we clearly see that a majority of people who answered their home country are from `India`, with the next highest group being the `Missing` category. Seeing how little there are in terms of people from other countries, I think using a cutoff of 50 responses seems reasonable - in essence, all countries with >50 responses will keep their country, while those with <50 responses will be combined.

Also note that the conversion rate for those who didn't put in a country were slightly more favorable (56:44 split between No:Yes). Thus, we'll keep the `Missing` category.

In [61]:
# Combine countries
country_agg = data.fillna("Missing").groupby(["Country"])["Converted"].count().loc[lambda x: x < 50].index
data.loc[data["Country"].isin(country_agg), "Country"] = "Country_Joined"
data["Country"].fillna("Missing", inplace=True)

# Check results
data.groupby(["Country", "Converted"])["Converted"].count()

Country               Converted
Country_Joined        0             119
                      1              46
India                 0            4091
                      1            2401
Missing               0            1385
                      1            1076
United Arab Emirates  0              33
                      1              20
United States         0              51
                      1              18
Name: Converted, dtype: int64

Now, we have only 5 categories for `Country`, and no more missing data!

### City

Next, we'll look into the `City` column.

In [54]:
data.fillna("Missing").groupby(["City", "Converted"])["Converted"].count()

City                         Converted
Missing                      0            1266
                             1             154
Mumbai                       0            1913
                             1            1309
Other Cities                 0             410
                             1             276
Other Cities of Maharashtra  0             256
                             1             201
Other Metro Cities           0             225
                             1             155
Select                       0            1146
                             1            1103
Thane & Outskirts            0             414
                             1             338
Tier II Cities               0              49
                             1              25
Name: Converted, dtype: int64

Across the board, we generally see that there are "enough" observations per column. Surprisingly, the `Select` column almost has a 50-50 ratio of 0s and 1s. Additionally, those who didn't put a value (IE had a value of `NA`) for their city were much more likely to not convert. This is probably because the cities mainly refer to those in India. Thus, we'll keep all values as `Missing`.

In [62]:
data["City"].fillna("Missing", inplace=True)

### Last Notable Activity

We found earlier that `Last Notable Activity` had a somewhat high correlation with `Converted`, but that there were also 16 total columns. Let's try to reduce this.

In [63]:
data.fillna("Missing").groupby(["Last Notable Activity", "Converted"])["Converted"].count()

Last Notable Activity    Converted
Email Bounced            0              51
                         1               9
Email Link Clicked       0             128
                         1              45
Email Opened             0            1783
                         1            1044
LNA_joined               0              46
                         1              54
Modified                 0            2624
                         1             783
Olark Chat Conversation  0             158
                         1              25
Page Visited on Website  0             225
                         1              93
SMS Sent                 0             664
                         1            1508
Name: Converted, dtype: int64

We see that there are several instances where there is only 1 outcome for a particular category (EX: `Approcahed upfront` only has 1 response of yes). Using the same application as before, if there are under 50 observations, we'll combine them into 1 group.

Also note that there were no missing observations!

In [64]:
# Combine Last Notable Activity
LNA_agg = data.fillna("Missing").groupby(["Last Notable Activity"])["Converted"].count().loc[lambda x: x < 50].index
data.loc[data["Last Notable Activity"].isin(LNA_agg), "Last Notable Activity"] = "LNA_joined"
data.groupby(["Last Notable Activity", "Converted"])["Converted"].count()

Last Notable Activity    Converted
Email Bounced            0              51
                         1               9
Email Link Clicked       0             128
                         1              45
Email Opened             0            1783
                         1            1044
LNA_joined               0              46
                         1              54
Modified                 0            2624
                         1             783
Olark Chat Conversation  0             158
                         1              25
Page Visited on Website  0             225
                         1              93
SMS Sent                 0             664
                         1            1508
Name: Converted, dtype: int64

Now, we see that the `LNA_joined` group tends to have a lot more people who more likely convert!

### Lead Profile

Now, we'll look at the `Lead Profile` column. It had high levels of missing data.

In [59]:
data.fillna("Missing").groupby(["Lead Profile", "Converted"])["Converted"].count()

Lead Profile                 Converted
Dual Specialization Student  1              20
Lateral Student              0               1
                             1              23
Missing                      0            2339
                             1             370
Other Leads                  0             307
                             1             180
Potential Lead               0             346
                             1            1267
Select                       0            2454
                             1            1692
Student of SomeSchool        0             232
                             1               9
Name: Converted, dtype: int64

We see that those who are specific students (`Dual Specialization Student` or `Lateral Student`), while low in county, have a high proportion of conversions. However, `Student of SomeSchool` does not share this trait, so we cannot combine all students into one category. Additionally, those who didn't put in a value (IE `Missing` above) clearly are less likely to convert.

In [65]:
spec_student_agg = ["Dual Specialization Student", "Lateral Student"]
data.loc[data["Lead Profile"].isin(spec_student_agg), "Lead Profile"] = "Dual Spec / Lat Student"
data["Lead Profile"].fillna("Missing", inplace=True)
data.fillna("Missing").groupby(["Lead Profile", "Converted"])["Converted"].count()

Lead Profile             Converted
Dual Spec / Lat Student  0               1
                         1              43
Missing                  0            2339
                         1             370
Other Leads              0             307
                         1             180
Potential Lead           0             346
                         1            1267
Select                   0            2454
                         1            1692
Student of SomeSchool    0             232
                         1               9
Name: Converted, dtype: int64